https://pypi.org/project/yfinance/

https://towardsdatascience.com/how-to-get-stock-data-using-python-c0de1df17e75

https://towardsdatascience.com/python-how-to-get-live-market-data-less-than-0-1-second-lag-c85ee280ed93

beta - https://bcs-express.ru/novosti-i-analitika/koeffitsienty-al-fa-i-beta-vybiraem-aktsii-v-portfel-po-nauke

In [286]:
import pandas as pd
import yfinance as yf
import plotly.graph_objs as go
import time
from tqdm import tqdm
import os
# отображать всю информацию в ячейке датафрейма
pd.set_option('display.max_colwidth', None)

In [287]:
path = '../../data/invest/'

In [392]:
vanguard_tickers = 'VOO VITAX VOOG VTI IVOO BNDW BNDX VWOB VT VEA EDV BIV VGIT VGLT BSV BND VIG ESGV VUG VYM VV MGC VDE VGT VOX'
etf_tickers_1 = 'IVV VTI VOO QQQ VEA AGG IEFA GLD EEM EFA VWO'

In [379]:
data = yf.download(tickers=tickers, 
                   #period='10y', 
                   start='2010-1-1',
                   end='2021-8-1',
                   interval='1d',
                  )
data.head(3)

[*********************100%***********************]  25 of 25 completed


Adj Close                                                       \
                  BIV        BND BNDW BNDX        BSV        EDV ESGV IVOO   
Date                                                                         
2009-12-31  52.957336  56.679153  NaN  NaN  64.769005  48.005615  NaN  NaN   
2010-01-04  53.171677  56.744041  NaN  NaN  64.825974  47.561291  NaN  NaN   
2010-01-05  53.452988  56.909920  NaN  NaN  64.988869  47.999527  NaN  NaN   

                                  ... Volume                                   \
                  MGC        VDE  ...  VITAX VOO VOOG    VOX      VT      VTI   
Date                              ...                                           
2009-12-31  30.775745  62.816113  ...    0.0 NaN  NaN  12100  135400  1322000   
2010-01-04  31.239378  64.775093  ...    0.0 NaN  NaN  19500  367700  2251500   
2010-01-05  31.335310  65.438156  ...    0.0 NaN  NaN  62800  994000  1597700   

                                        
               VUG      VV VWOB    VYM  
Date                                    
2009-12-31  245900  509100  NaN  46000  
2010-01-04  496200  180300  NaN  65600  
2010-01-05  736200  210700  NaN  47100  

[3 rows x 150 columns]

In [393]:
data = yf.download(tickers=etf_tickers_1, 
                   #period='10y', 
                   start='2010-1-1',
                   end='2021-8-1',
                   interval='1d',
                  )
data.head(3)

[*********************100%***********************]  11 of 11 completed


Adj Close                                                    \
                  AGG        EEM        EFA         GLD IEFA        IVV   
Date                                                                      
2009-12-31  75.984985  32.998432  39.444958  107.309998  NaN  89.363083   
2010-01-04  76.073387  33.960560  40.479599  109.800003  NaN  90.833710   
2010-01-05  76.419418  34.207054  40.515278  109.699997  NaN  91.097466   

                                                 ...    Volume            \
                  QQQ        VEA VOO        VTI  ...       EEM       EFA   
Date                                             ...                       
2009-12-31  40.871811  24.367882 NaN  45.326057  ...  36499500  13893400   
2010-01-04  41.470360  25.023403 NaN  46.081886  ...  70761600  18556900   
2010-01-05  41.470360  25.037651 NaN  46.258789  ...  50196300  14352800   

                                                                              
                 GLD IEFA      IVV       QQQ      VEA VOO      VTI       VWO  
Date                                                                          
2009-12-31   9124700  NaN  3000900  50079200   902000 NaN  1322000   4666600  
2010-01-04  16224100  NaN  3574200  62822800  2165800 NaN  2251500  16750400  
2010-01-05  14213100  NaN  2784100  62935600   881800 NaN  1597700  13083300  

[3 rows x 66 columns]

In [271]:
indexes ='^GSPC'
index_data = yf.download(tickers=indexes, 
                   #period='10y', 
                   start='2010-1-1',
                   end='2021-8-1',
                   interval='1d',
                  )
index_data.head(3)

[*********************100%***********************]  1 of 1 completed


Open         High          Low        Close    Adj Close  \
Date                                                                          
2009-12-31  1126.599976  1127.640015  1114.810059  1115.099976  1115.099976   
2010-01-04  1116.560059  1133.869995  1116.560059  1132.989990  1132.989990   
2010-01-05  1132.660034  1136.630005  1129.660034  1136.520020  1136.520020   

                Volume  
Date                    
2009-12-31  2076990000  
2010-01-04  3991400000  
2010-01-05  2491020000

# Сравнение бумаг

In [399]:
# сравнительная таблица
df_compare = pd.DataFrame(columns=['symbol', 'short Name', 'quote Type', 'fund Family', 'market', '3year Av. Return',
                                  '5 year Av.Return', 'av. Vol 10days', 'market Cap', 'Avg. Volume', 'Inception Date',
                                   'Net Assets', 'Beta (5Y Monthly)'
                                   
                                  ])
i = 0
for ticker in tqdm(etf_tickers_1.split()):
    paper = yf.Ticker(ticker)
    #time.sleep(2)
    try:
        df_compare.loc[i] = [
            paper.info['symbol'], paper.info['shortName'], paper.info['quoteType'], paper.info['fundFamily'],
            paper.info['market'], paper.info['threeYearAverageReturn'], paper.info['fiveYearAverageReturn'], 
            paper.info['averageVolume10days'], paper.info['marketCap'], 
            paper.major_holders.iloc[7, 1] if paper.info['quoteType'] == 'ETF' else None,
            paper.institutional_holders.iloc[7, 1] if paper.info['quoteType'] == 'ETF' else None,
            paper.institutional_holders.iloc[0, 1] if paper.info['quoteType'] == 'ETF' else None,
            paper.institutional_holders.iloc[5, 1] if paper.info['quoteType'] == 'ETF' else None,
                            ]
        i += 1
    except Exception:
        print('Ошибка с тикером: ', ticker)
    
df_compare

100%|██████████████████████████████████████████████████████████████████████████████████| 11/11 [00:34<00:00,  3.10s/it]


symbol                       short Name quote Type  \
0     IVV         iShares Core S&P 500 ETF        ETF   
1     VTI  Vanguard Total Stock Market ETF        ETF   
2     VOO             Vanguard S&P 500 ETF        ETF   
3     QQQ      Invesco QQQ Trust, Series 1        ETF   
4     VEA  Vanguard FTSE Developed Markets        ETF   
5     AGG  iShares Core U.S. Aggregate Bon        ETF   
6    IEFA       iShares Core MSCI EAFE ETF        ETF   
7     GLD                  SPDR Gold Trust        ETF   
8     EEM  iShares MSCI Emerging Index Fun        ETF   
9     EFA            iShares MSCI EAFE ETF        ETF   
10    VWO  Vanguard FTSE Emerging Markets         ETF   

                          fund Family     market  3year Av. Return  \
0                             iShares  us_market            0.1808   
1                            Vanguard  us_market            0.1811   
2                            Vanguard  us_market            0.1809   
3                             Invesco  us_market            0.2807   
4                            Vanguard  us_market            0.0947   
5                             iShares  us_market            0.0565   
6                             iShares  us_market            0.0901   
7   SPDR State Street Global Advisors  us_market            0.1352   
8                             iShares  us_market            0.0837   
9                             iShares  us_market            0.0870   
10                           Vanguard  us_market            0.0908   

    5 year Av.Return av. Vol 10days market Cap Avg. Volume Inception Date  \
0             0.1738        3252012       None     4297942     2000-05-15   
1             0.1747        3011950       None     3528425     2001-05-24   
2             0.1738        3825712       None     3893671     2010-09-07   
3             0.2696       31431825       None    38895406     1999-03-10   
4             0.1053        6364312       None     7264978     2007-07-20   
5             0.0319        4857887       None     5615843     2003-09-22   
6             0.1047        5923962       None     7461945     2012-10-18   
7             0.0566        8869037       None     8758273     2004-11-18   
8             0.0979       39372837       None    33970815     2003-04-07   
9             0.0999       18421650       None    20640095     2001-08-14   
10            0.0949       10701150       None     8732604     2005-03-04   

   Net Assets Beta (5Y Monthly)  
0     294.95B              1.00  
1       1.26T              1.04  
2     753.41B              1.00  
3     174.51B              1.02  
4     157.48B              1.04  
5       88.8B              1.00  
6      95.78B              1.01  
7      59.26B              0.09  
8      30.33B              0.99  
9      56.77B              0.99  
10    117.28B              0.96

In [400]:
# Конвертим в числовой формат
df_compare["Beta (5Y Monthly)"] = pd.to_numeric(df_compare["Beta (5Y Monthly)"])
df_compare["Avg. Volume"] = pd.to_numeric(df_compare["Avg. Volume"])
df_compare["5 year Av.Return"] = pd.to_numeric(df_compare["5 year Av.Return"])
df_compare["3year Av. Return"] = pd.to_numeric(df_compare["3year Av. Return"])
df_compare["Inception Date"] = pd.to_datetime(df_compare["Inception Date"])

In [401]:
# сохраняем
df_compare.to_pickle(os.path.join(path, 'df_compare_biggest_etf.pkl'))

In [293]:
# подгружаем данные
df_compare = pd.read_pickle(os.path.join(path, 'df_compare.pkl'))
print(df_compare.shape)
df_compare.head(3)

(24, 13)


symbol                       short Name  quote Type fund Family     market  \
0    VOO             Vanguard S&P 500 ETF         ETF    Vanguard  us_market   
1  VITAX  Vanguard Information Technology  MUTUALFUND        None  us_market   
2   VOOG      Vanguard S&P 500 Growth ETF         ETF    Vanguard  us_market   

  3year Av. Return 5 year Av.Return av. Vol 10days market Cap Avg. Volume  \
0           0.1809           0.1738        3825712       None     3893671   
1             None             None              0       None        None   
2             0.23           0.2163          95587       None       92359   

  Inception Date Net Assets Beta (5Y Monthly)  
0     2010-09-07    753.41B              1.00  
1           None       None              None  
2     2010-09-07      5.99B              0.98

In [402]:
df_compare.style.bar(
    subset=["3year Av. Return", "5 year Av.Return", "Avg. Volume", "Beta (5Y Monthly)", 'av. Vol 10days', ],
    color='#DCFFD3')

In [357]:
type(df_compare.iloc[23, -3])

pandas._libs.tslibs.timestamps.Timestamp

# Описание бумаг

In [295]:
# Описание бумаги
df_info = pd.DataFrame(columns=['symbol', 'shortName', 'longBusinessSummary'])
i = 0
for ticker in tqdm(tickers.split()):
    paper = yf.Ticker(ticker)
    #time.sleep(1)
    try:
        df_info.loc[i] = [paper.info['symbol'], paper.info['shortName'], paper.info['longBusinessSummary']]
        i += 1
    except Exception:
        print('Ошибка с тикером: ', ticker)
df_info

 16%|█████████████▎                                                                     | 4/25 [00:26<02:18,  6.58s/it]

Ошибка с тикером:  VTI


 40%|████████████████████████████████▊                                                 | 10/25 [01:05<01:37,  6.51s/it]

Ошибка с тикером:  VEA


100%|██████████████████████████████████████████████████████████████████████████████████| 25/25 [02:51<00:00,  6.86s/it]


symbol                        shortName  \
0     VOO             Vanguard S&P 500 ETF   
1   VITAX  Vanguard Information Technology   
2    VOOG      Vanguard S&P 500 Growth ETF   
3    IVOO     Vanguard S&P Mid-Cap 400 ETF   
4    BNDW    Vanguard Total World Bond ETF   
5    BNDX  Vanguard Total International Bo   
6    VWOB  Vanguard Emerging Markets Gover   
7      VT  Vanguard Total World Stock Inde   
8     EDV  Vanguard Extended Duration Trea   
9     BIV  Vanguard Intermediate-Term Bond   
10   VGIT  Vanguard Intermediate-Term Trea   
11   VGLT       Vanguard Long-Treasury ETF   
12    BSV     Vanguard Short-Term Bond ETF   
13    BND   Vanguard Total Bond Market ETF   
14    VIG    Vanguard Div Appreciation ETF   
15   ESGV      Vanguard ESG U.S. Stock ETF   
16    VUG              Vanguard Growth ETF   
17    VYM  Vanguard High Dividend Yield ET   
18     VV           Vanguard Large-Cap ETF   
19    MGC            Vanguard Mega Cap ETF   
20    VDE              Vanguard Energy ETF   
21    VGT    Vanguard Information Tech ETF   
22    VOX  Vanguard Communication Services   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               longBusinessSummary  
0                                                The investment seeks to track the performance of the Standard & Poorâs 500 Index that measures the investment return of large-capitalization stocks.\n The fund employs an indexing investment approach designed to track the performance of the Standard & Poor&#39;s 500 Index, a widely recognized benchmark of U.S. stock market performance that is dominated by the stocks of large U.S. companies. The advisor attempts to replicate the target index by investing all, or substantially all, of its assets in the stocks that make up the index, holding each stock in approximately the same proportion as its weighting in the index.  
1    The investment seeks to track the performance of a benchmark index.  The fund employs an indexing investment approach designed to track the performance of the MSCI US Investable Market Index/Information Technology 25/50, an index made up of stocks of large, mid-size, and small U.S. companies within the information technology sector, as classified under the Global Industry Classification Standard. The Advisor attempts to replicate the target index by seeking to invest all, or substantially all, of its assets in the stocks that make up the index, in order to hold each stock in approximately the same proportion as its weighting in the index. It is non-diversified.  
2                                                                                                                                                                                                        The investment seeks to track the performance of a benchmark index that measures the investment return of large-capitalization growth stocks in the United States.\n The fund employs an indexing investment approach designed to track the performance of the S&P 500Â® Growth Index, which represents the growth companies, as determined by the index sponsor, of the S&P 500 Index. The index measures the performance of large-capitalization growth companies in the United States.  
3                                                                                               The investment seeks to track the performance of a benchmark index that measures the investmen

In [296]:
# сохраняем
df_info.to_pickle(os.path.join(path, 'df_info.pkl'))

In [297]:
# подгружаем данные
df_info = pd.read_pickle(os.path.join(path, 'df_info.pkl'))
print(df_info.shape)
df_info.head(3)

(23, 3)


symbol                        shortName  \
0    VOO             Vanguard S&P 500 ETF   
1  VITAX  Vanguard Information Technology   
2   VOOG      Vanguard S&P 500 Growth ETF   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             longBusinessSummary  
0                                              The investment seeks to track the performance of the Standard & Poorâs 500 Index that measures the investment return of large-capitalization stocks.\n The fund employs an indexing investment approach designed to track the performance of the Standard & Poor&#39;s 500 Index, a widely recognized benchmark of U.S. stock market performance that is dominated by the stocks of large U.S. companies. The advisor attempts to replicate the target index by investing all, or substantially all, of its assets in the stocks that make up the index, holding each stock in approximately the same proportion as its weighting in the index.  
1  The investment seeks to track the performance of a benchmark index.  The fund employs an indexing investment approach designed to track the performance of the MSCI US Investable Market Index/Information Technology 25/50, an index made up of stocks of large, mid-size, and small U.S. companies within the information technology sector, as classified under the Global Industry Classification Standard. The Advisor attempts to replicate the target index by seeking to invest all, or substantially all, of its assets in the stocks that make up the index, in order to hold each stock in approximately the same proportion as its weighting in the index. It is non-diversified.  
2                                                                                                                                                                                                      The investment seeks to track the performance of a benchmark index that measures the investment return of large-capitalization growth stocks in the United States.\n The fund employs an indexing investment approach designed to track the performance of the S&P 500Â® Growth Index, which represents the growth companies, as determined by the index sponsor, of the S&P 500 Index. The index measures the performance of large-capitalization growth companies in the United States.

# Построение графиков

In [394]:
# Нормализация цены: разделим цены закрытия на первую цену по тикеру в датафрейме
for ticker in etf_tickers_1.split():
    data['Norm price', ticker] = data['Close', ticker] \
                                 / data['Close', ticker].loc[data['Close', ticker].first_valid_index()]
    print('Начальная цена в DF для: ', 
          ticker, data['Close', ticker].loc[data['Close', ticker].first_valid_index()],
         'Текущая цена: ', 
          data['Close', ticker].loc[data['Close', ticker].last_valid_index()],
          'Увеличение в раз: ',
          data['Close', ticker].loc[data['Close', ticker].last_valid_index()] \
          / data['Close', ticker].loc[data['Close', ticker].first_valid_index()],
         )
data.tail(3)

Начальная цена в DF для:  IVV 111.80999755859375 Текущая цена:  440.3999938964844 Увеличение в раз:  3.9388248234751444
Начальная цена в DF для:  VTI 56.369998931884766 Текущая цена:  226.69000244140625 Увеличение в раз:  4.021465437942075
Начальная цена в DF для:  VOO 101.31999969482422 Текущая цена:  403.1499938964844 Увеличение в раз:  3.9789774487837732
Начальная цена в DF для:  QQQ 45.75 Текущая цена:  364.57000732421875 Увеличение в раз:  7.9687433294911205
Начальная цена в DF для:  VEA 34.20000076293945 Текущая цена:  51.779998779296875 Увеличение в раз:  1.5140350182508722
Начальная цена в DF для:  AGG 103.19000244140625 Текущая цена:  116.45999908447266 Увеличение в раз:  1.128597696764291
Начальная цена в DF для:  IEFA 47.540000915527344 Текущая цена:  75.55000305175781 Увеличение в раз:  1.58918808575542
Начальная цена в DF для:  GLD 107.30999755859375 Текущая цена:  169.82000732421875 Увеличение в раз:  1.5825180429390382
Начальная цена в DF для:  EEM 41.5 Текущая цена:  51

Adj Close                                               \
                   AGG        EEM        EFA         GLD       IEFA   
Date                                                                  
2021-07-28  116.322952  51.840000  79.349998  169.289993  75.470001   
2021-07-29  116.133232  52.099998  79.900002  171.169998  75.989998   
2021-07-30  116.292999  51.599998  79.489998  169.820007  75.550003   

                                                                       ...  \
                   IVV         QQQ        VEA         VOO         VTI  ...   
Date                                                                   ...   
2021-07-28  440.679993  365.829987  51.730000  403.390015  227.039993  ...   
2021-07-29  442.640015  366.480011  52.119999  405.130005  228.039993  ...   
2021-07-30  440.399994  364.570007  51.779999  403.149994  226.690002  ...   

           Norm price                                                    \
                  VTI       VOO       QQQ       VEA       AGG      IEFA   
Date                                                                      
2021-07-28   4.027674  3.981346  7.996284  1.512573  1.128888  1.587505   
2021-07-29   4.045414  3.998520  8.010492  1.523977  1.127047  1.598443   
2021-07-30   4.021465  3.978977  7.968743  1.514035  1.128598  1.589188   

                                                    
                 GLD       EEM       EFA       VWO  
Date                                                
2021-07-28  1.577579  1.249157  1.435420  1.250732  
2021-07-29  1.595098  1.255422  1.445369  1.255122  
2021-07-30  1.582518  1.243373  1.437952  1.246585  

[3 rows x 77 columns]

In [395]:
def stock_plot(tickers, df, column):
    """
    tickers: List - список бумаг
    df: Pandas DataFrame - датафрейм цен акций
    column: str, имя столбца, которое брать для цены
    """
    #declare figure
    fig = go.Figure()

    for ticker in tickers.split():
        #Candlestick
        fig.add_trace(go.Scatter(x=df.index,
                                 y=df[column, ticker],
                                 name=ticker))
    # Add titles
    fig.update_layout(
        #title='Uber live share price evolution',
        yaxis_title=f'{column} per Shares')

    return fig.show()

# 'Norm price' 'Close'
stock_plot(etf_tickers_1, data, 'Close')

In [398]:
stock_plot(etf_tickers_1, data, 'Norm price')